# Imports

In [1]:
# General

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

# Hyperparameter tuning
import optuna

# Models
import lightgbm as lgb
import xgboost as xgb
from catboost import CatBoostClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import StackingClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.linear_model import SGDClassifier

# Data processing
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import OrdinalEncoder, OneHotEncoder
from sklearn.model_selection import train_test_split
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline

# Metrics
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import cross_val_score

# Data preparation

In [2]:
# Data input

try:
    data = pd.read_csv('../data/train.csv')
    data_to_predict = pd.read_csv('../data/test.csv')
    data_ccrisk = pd.read_csv('../data/credit_risk_dataset.csv')

except:
    data = pd.read_csv('/kaggle/input/playground-series-s4e10/train.csv')
    data_to_predict = pd.read_csv('/kaggle/input/playground-series-s4e10/test.csv')
    data_ccrisk = pd.read_csv('/kaggle/input/loan-approval-prediction/credit_risk_dataset.csv')


data_ccrisk.dropna(inplace=True)
data_ccrisk.drop_duplicates(inplace=True)

X_old = data.drop(['loan_status'], axis=1)
y_old = data['loan_status']

# Merge the dataframes
data_no_id = data.drop(['id'], axis=1)
merged_data = pd.concat([data_no_id, data_ccrisk], ignore_index=True)

X = merged_data.drop(['loan_status'], axis=1)
y = merged_data['loan_status']

X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, shuffle=True, test_size=0.2, random_state=2024)

In [3]:
# Data processing
categorical_columns = X.select_dtypes(include=['object']).columns
categorical_ordinal = ['loan_grade']
categorical_onehot = categorical_columns.drop(categorical_ordinal)

numerical_columns = X.select_dtypes(include=['int64', 'float64']).columns

# Preprocessor
preprocessor = ColumnTransformer(
	transformers=[
		('ordinal', OrdinalEncoder(), categorical_ordinal),
		('onehot', OneHotEncoder(), categorical_onehot),
		('scaler', StandardScaler(), numerical_columns)
	])

preprocessor.fit(X_train)

X_train_prep = preprocessor.transform(X_train)
X_test_prep = preprocessor.transform(X_test)

# Models

## XGBoost

In [4]:
def xgb_objective(trial):
    # Hyperparameter search space
    param = {
        'max_depth': trial.suggest_int('max_depth', 3, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'n_estimators': trial.suggest_int('n_estimators', 100, 500),
        'subsample': trial.suggest_float('subsample', 0.6, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
        'gamma': trial.suggest_float('gamma', 0.0, 0.5),
        'lambda': trial.suggest_float('lambda', 1e-8, 10.0, log=True),
        'alpha': trial.suggest_float('alpha', 1e-8, 10.0, log=True),
        'scale_pos_weight': trial.suggest_float('scale_pos_weight', 1.0, 3.0),
        'eval_metric': 'auc',  # AUC is the metric
        'objective': 'binary:logistic'  # Use binary logistic, probability outputs
    }

    # Initialize the model
    model = xgb.XGBClassifier(**param)

    # Fit the model
    model.fit(X_train_prep, y_train, 
              eval_set=[(X_test_prep, y_test)],  
              verbose=False)

    # Predict proba for validation set
    y_pred_prob = model.predict_proba(X_test_prep)[:, 1]

    auc = roc_auc_score(y_test, y_pred_prob)
 
    return auc

# Study object to run the optimization. I want to maximize AUC
xgb_study = optuna.create_study(direction='maximize')
xgb_study.optimize(xgb_objective, n_trials=500, timeout=3600*2.5)

print(f"Best trial: {xgb_study.best_trial.params}")

[I 2024-10-23 19:36:28,510] A new study created in memory with name: no-name-ed7e2ef0-5652-41f5-b377-da65bea7e3ec
[I 2024-10-23 19:36:32,677] Trial 0 finished with value: 0.9547373173974808 and parameters: {'max_depth': 3, 'learning_rate': 0.1038555924331226, 'n_estimators': 498, 'subsample': 0.7180935493787023, 'colsample_bytree': 0.5688477191140773, 'gamma': 0.0666293126029831, 'lambda': 1.2864735322743417e-05, 'alpha': 1.9242268704828993e-05, 'scale_pos_weight': 1.670267090366927}. Best is trial 0 with value: 0.9547373173974808.
[I 2024-10-23 19:36:35,696] Trial 1 finished with value: 0.9551550301615135 and parameters: {'max_depth': 9, 'learning_rate': 0.10847181310007674, 'n_estimators': 242, 'subsample': 0.9742987803665153, 'colsample_bytree': 0.6951867638618081, 'gamma': 0.27034696927929885, 'lambda': 7.252925083156773e-08, 'alpha': 1.8692458435385953e-05, 'scale_pos_weight': 1.6309447062448084}. Best is trial 1 with value: 0.9551550301615135.
[I 2024-10-23 19:36:38,147] Trial 2 

Best trial: {'max_depth': 6, 'learning_rate': 0.09883485070489191, 'n_estimators': 288, 'subsample': 0.9835063079624086, 'colsample_bytree': 0.6824653208322442, 'gamma': 0.27886770251477494, 'lambda': 0.0003745285956051325, 'alpha': 1.1931032382768336, 'scale_pos_weight': 2.488394052746385}


In [5]:
xgb_best_params = xgb_study.best_trial.params
xgb_best_score = xgb_study.best_trial.value
xgb_best_score

0.9581947548348121

## CatBoostClassifier

In [6]:
from catboost import CatBoostClassifier

def cat_objective(trial):

    # Define the hyperparameter search space

    param = {
        'depth': trial.suggest_int('depth', 4, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'iterations': trial.suggest_int('iterations', 200, 1000),
        'l2_leaf_reg': trial.suggest_float('l2_leaf_reg', 1e-8, 10.0, log=True),
        'border_count': trial.suggest_int('border_count', 32, 255),
        'bagging_temperature': trial.suggest_float('bagging_temperature', 0.0, 1.0),
        'random_strength': trial.suggest_float('random_strength', 0.0, 1.0),
        'scale_pos_weight': trial.suggest_float('scale_pos_weight', 1.0, 3.0),
        'eval_metric': 'AUC',  
        'logging_level': 'Silent',  # Disable CatBoost output
        'task_type': 'CPU',  # Try using GPU
        'use_best_model': True
    }

    # Initialize the CatBoost model with the trial's parameters
    model = CatBoostClassifier(**param)

    # Fit the model
    model.fit(X_train_prep, y_train,
              eval_set=[(X_test_prep, y_test)],
              early_stopping_rounds=20,  # Early stopping to prevent overfitting
              verbose=False)

    # Get predictions and calculate AUC score
    y_pred_prob = model.predict_proba(X_test_prep)[:, 1]  # Probabilities for class 1

    auc = roc_auc_score(y_test, y_pred_prob)

    return aucaa

try:
    cat_study = optuna.create_study(direction='maximize')  # We want to maximize AUC
    
    cat_study.optimize(cat_objective, n_trials=500, timeout=3600*3)
    
    # Output the best trial
    print(f"Best trial: {cat_study.best_trial.params}")
    
except Exception as e:
    print(e)

[I 2024-10-23 20:05:09,765] A new study created in memory with name: no-name-1a03395e-6617-4d2f-b901-46288261bfd6
[W 2024-10-23 20:05:15,874] Trial 0 failed with parameters: {'depth': 5, 'learning_rate': 0.2449254154296146, 'iterations': 782, 'l2_leaf_reg': 2.686460263951953, 'border_count': 74, 'bagging_temperature': 0.3642919439246999, 'random_strength': 0.10946068706023493, 'scale_pos_weight': 1.0995667738648085} because of the following error: NameError("name 'aucaa' is not defined").
Traceback (most recent call last):
  File "/opt/conda/lib/python3.10/site-packages/optuna/study/_optimize.py", line 197, in _run_trial
    value_or_values = func(trial)
  File "/tmp/ipykernel_17/1517651619.py", line 36, in cat_objective
    return aucaa
NameError: name 'aucaa' is not defined
[W 2024-10-23 20:05:15,879] Trial 0 failed with value None.


name 'aucaa' is not defined


In [7]:
try:
    cat_best_params = cat_study.best_trial.params
    cat_best_score = cat_study.best_trial.value
    cat_best_score

except Exception as e:
    print(e)

No trials are completed yet.


## LightGBM

In [8]:
# Objective function for LightGBM

def lgb_objective(trial):
    param = {
        'objective': 'binary',
        'metric': 'auc',
        'boosting_type': 'gbdt',
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.3),
        'num_leaves': trial.suggest_int('num_leaves', 20, 150),  # Adjusted num_leaves range
        'max_depth': trial.suggest_int('max_depth', 3, 10),      # Reduced max_depth
        'min_child_samples': trial.suggest_int('min_child_samples', 1, 100),  # Reduced min_child_samples
        'min_child_weight': trial.suggest_float('min_child_weight', 1e-3, 10.0),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'min_gain_to_split': trial.suggest_float('min_gain_to_split', 0.0, 0.2),  # Added min_gain_to_split
    }

    lgb_model = lgb.LGBMClassifier(**param)

    # Train the model with early stopping
    lgb_model.fit(X_train_prep, y_train,
                  eval_set=[(X_test_prep, y_test)],
                  eval_metric='auc',
                  callbacks=[lgb.early_stopping(stopping_rounds=100)])

    # Predict and evaluate AUC
    y_pred_prob = lgb_model.predict_proba(X_test_prep)[:, 1]
    auc = roc_auc_score(y_test, y_pred_prob)

    return auc


# Optimize the objective function
lgb_study = optuna.create_study(direction='maximize')
lgb_study.optimize(lgb_objective, n_trials=500, timeout=3600*3)

# Best parameters and AUC
print("Best LGBM Params: ", lgb_study.best_trial.params)
print("Best AUC for LGBM: ", lgb_study.best_value)

[I 2024-10-23 20:05:16,150] A new study created in memory with name: no-name-44a9ce1a-17ef-42e0-aceb-7ede00255f8e


[LightGBM] [Warning] min_gain_to_split is set=0.060470696613267184, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.060470696613267184
[LightGBM] [Warning] min_gain_to_split is set=0.060470696613267184, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.060470696613267184
[LightGBM] [Info] Number of positive: 11630, number of negative: 58086
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.008674 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 957
[LightGBM] [Info] Number of data points in the train set: 69716, number of used features: 20
[LightGBM] [Warning] min_gain_to_split is set=0.060470696613267184, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.060470696613267184
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.166820 -> initscore=-1.608337
[LightGBM] [Info] Start

[I 2024-10-23 20:05:20,847] Trial 0 finished with value: 0.9583851054047484 and parameters: {'learning_rate': 0.24821216293536927, 'num_leaves': 146, 'max_depth': 7, 'min_child_samples': 93, 'min_child_weight': 6.7787650661886625, 'subsample': 0.5813735089856369, 'colsample_bytree': 0.6179897375654579, 'n_estimators': 809, 'min_gain_to_split': 0.060470696613267184}. Best is trial 0 with value: 0.9583851054047484.


[LightGBM] [Warning] min_gain_to_split is set=0.14246965947137144, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.14246965947137144
[LightGBM] [Warning] min_gain_to_split is set=0.14246965947137144, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.14246965947137144
[LightGBM] [Info] Number of positive: 11630, number of negative: 58086
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.017356 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 957
[LightGBM] [Info] Number of data points in the train set: 69716, number of used features: 20
[LightGBM] [Warning] min_gain_to_split is set=0.14246965947137144, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.14246965947137144
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.166820 -> initscore=-1.608337
[LightGBM] [Info] Start training from score -1.608337
[LightGBM] [Warning] No further splits 

[I 2024-10-23 20:05:28,216] Trial 1 finished with value: 0.9596511729014481 and parameters: {'learning_rate': 0.09353366474773407, 'num_leaves': 87, 'max_depth': 5, 'min_child_samples': 57, 'min_child_weight': 0.3183303012750799, 'subsample': 0.8826783823105084, 'colsample_bytree': 0.7157466053936503, 'n_estimators': 825, 'min_gain_to_split': 0.14246965947137144}. Best is trial 1 with value: 0.9596511729014481.


...

[LightGBM] [Warning] min_gain_to_split is set=0.004054005248843007, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.004054005248843007
[LightGBM] [Warning] min_gain_to_split is set=0.004054005248843007, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.004054005248843007
[LightGBM] [Info] Number of positive: 11630, number of negative: 58086
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.016411 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 957
[LightGBM] [Info] Number of data points in the train set: 69716, number of used features: 20
[LightGBM] [Warning] min_gain_to_split is set=0.004054005248843007, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.004054005248843007
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.166820 -> initscore=-1.608337
[LightGBM] [Info] Start training from score -1.608337
Training until validation scores 

[I 2024-10-23 21:00:39,361] Trial 498 finished with value: 0.9605335437557435 and parameters: {'learning_rate': 0.16016890456901617, 'num_leaves': 32, 'max_depth': 10, 'min_child_samples': 16, 'min_child_weight': 7.116116576959367, 'subsample': 0.9145820685231127, 'colsample_bytree': 0.5362449423129801, 'n_estimators': 682, 'min_gain_to_split': 0.004054005248843007}. Best is trial 402 with value: 0.961439215594155.


[LightGBM] [Warning] min_gain_to_split is set=0.00648510513737164, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.00648510513737164
[LightGBM] [Warning] min_gain_to_split is set=0.00648510513737164, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.00648510513737164
[LightGBM] [Info] Number of positive: 11630, number of negative: 58086
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.016502 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 957
[LightGBM] [Info] Number of data points in the train set: 69716, number of used features: 20
[LightGBM] [Warning] min_gain_to_split is set=0.00648510513737164, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.00648510513737164
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.166820 -> initscore=-1.608337
[LightGBM] [Info] Start training from score -1.608337
Training until validation scores don't 

[I 2024-10-23 21:00:45,733] Trial 499 finished with value: 0.9610959878357498 and parameters: {'learning_rate': 0.09951851399798643, 'num_leaves': 25, 'max_depth': 10, 'min_child_samples': 6, 'min_child_weight': 9.572295130121084, 'subsample': 0.9000484332427744, 'colsample_bytree': 0.5704069985241903, 'n_estimators': 629, 'min_gain_to_split': 0.00648510513737164}. Best is trial 402 with value: 0.961439215594155.


Best LGBM Params:  {'learning_rate': 0.12655042458722948, 'num_leaves': 30, 'max_depth': 10, 'min_child_samples': 61, 'min_child_weight': 8.320024654770164, 'subsample': 0.8998816732345819, 'colsample_bytree': 0.5435367315748005, 'n_estimators': 709, 'min_gain_to_split': 0.0038687550899640334}
Best AUC for LGBM:  0.961439215594155


In [9]:
lgb_best_params = lgb_study.best_trial.params
lgb_best_score = lgb_study.best_value
lgb_best_score

0.961439215594155

## ExtraTreesClassifier

In [10]:
from sklearn.ensemble import ExtraTreesClassifier

def extratrees_objective(trial):
    param = {
        'n_estimators': trial.suggest_int('n_estimators', 100, 500),
        'max_depth': trial.suggest_int('max_depth', 5, 20),
        'min_samples_split': trial.suggest_int('min_samples_split', 2, 10),
        'min_samples_leaf': trial.suggest_int('min_samples_leaf', 1, 10),
        'max_features': trial.suggest_float('max_features', 0.1, 1.0)
    }

    model = ExtraTreesClassifier(**param)
    score = cross_val_score(model, X_train_prep, y_train, cv=3, scoring='roc_auc').mean()

    return score

extratrees_study = optuna.create_study(direction='maximize')
extratrees_study.optimize(extratrees_objective, n_trials=200, timeout=1800)

print('Best parameters for ExtraTrees:', extratrees_study.best_params)

[I 2024-10-23 21:00:50,954] A new study created in memory with name: no-name-1d54d93e-d32e-411c-a60b-443cf11dd1c0
[I 2024-10-23 21:01:27,579] Trial 0 finished with value: 0.9296124655515882 and parameters: {'n_estimators': 111, 'max_depth': 14, 'min_samples_split': 3, 'min_samples_leaf': 8, 'max_features': 0.9556739801943192}. Best is trial 0 with value: 0.9296124655515882.
[I 2024-10-23 21:01:52,906] Trial 1 finished with value: 0.8862308226631098 and parameters: {'n_estimators': 350, 'max_depth': 6, 'min_samples_split': 9, 'min_samples_leaf': 2, 'max_features': 0.22374462276477547}. Best is trial 0 with value: 0.9296124655515882.
[I 2024-10-23 21:03:19,134] Trial 2 finished with value: 0.9213531016405914 and parameters: {'n_estimators': 489, 'max_depth': 14, 'min_samples_split': 3, 'min_samples_leaf': 10, 'max_features': 0.4431603116949975}. Best is trial 0 with value: 0.9296124655515882.
[I 2024-10-23 21:05:34,911] Trial 3 finished with value: 0.9291912801672476 and parameters: {'n_

Best parameters for ExtraTrees: {'n_estimators': 170, 'max_depth': 17, 'min_samples_split': 7, 'min_samples_leaf': 1, 'max_features': 0.8721858323954309}


In [11]:
extratrees_best_params = extratrees_study.best_params
extratrees_best_score = extratrees_study.best_value
extratrees_best_score

0.9315187185991398

## HistGradientBoostingClassifier

In [12]:
from sklearn.experimental import enable_hist_gradient_boosting
from sklearn.ensemble import HistGradientBoostingClassifier

def histgb_objective(trial):
    param = {
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1, log=True),
        'max_iter': trial.suggest_int('max_iter', 100, 500),
        'max_depth': trial.suggest_int('max_depth', 5, 20),
        'min_samples_leaf': trial.suggest_int('min_samples_leaf', 10, 50),
        'max_leaf_nodes': trial.suggest_int('max_leaf_nodes', 10, 50),
        'l2_regularization': trial.suggest_float('l2_regularization', 1e-5, 1.0, log=True)
    }

    model = HistGradientBoostingClassifier(**param)
    score = cross_val_score(model, X_train_prep, y_train, cv=3, scoring='roc_auc').mean()

    return score

histgb_study = optuna.create_study(direction='maximize')
histgb_study.optimize(histgb_objective, n_trials=200, timeout=3600)
print('Best parameters for HistGradientBoosting:', histgb_study.best_params)

/opt/conda/lib/python3.10/site-packages/sklearn/experimental/enable_hist_gradient_boosting.py:16: UserWarning: Since version 1.0, it is not needed to import enable_hist_gradient_boosting anymore. HistGradientBoostingClassifier and HistGradientBoostingRegressor are now stable and can be normally imported from sklearn.ensemble.
  warnings.warn(
[I 2024-10-23 21:31:02,267] A new study created in memory with name: no-name-7ed2a63a-6c3f-4ac3-813f-7dcd26f426c8
[I 2024-10-23 21:31:09,909] Trial 0 finished with value: 0.9515462993665277 and parameters: {'learning_rate': 0.08106381259803816, 'max_iter': 180, 'max_depth': 15, 'min_samples_leaf': 37, 'max_leaf_nodes': 32, 'l2_regularization': 0.014673601353403017}. Best is trial 0 with value: 0.9515462993665277.
[I 2024-10-23 21:31:25,288] Trial 1 finished with value: 0.9514168643419367 and parameters: {'learning_rate': 0.03312345121161616, 'max_iter': 231, 'max_depth': 20, 'min_samples_leaf': 44, 'max_leaf_nodes': 43, 'l2_regularization': 2.4620

Best parameters for HistGradientBoosting: {'learning_rate': 0.05241807549870634, 'max_iter': 320, 'max_depth': 12, 'min_samples_leaf': 46, 'max_leaf_nodes': 45, 'l2_regularization': 0.0010994373016020706}


In [13]:
histgb_best_params = histgb_study.best_trial.params
histgb_best_score = histgb_study.best_trial.value
histgb_best_score

0.9525622454153471

## KNN

In [14]:
from sklearn.neighbors import KNeighborsClassifier

def knn_objective(trial):
    param = {
        'n_neighbors': trial.suggest_int('n_neighbors', 3, 15),
        'leaf_size': trial.suggest_int('leaf_size', 20, 50),
        'p': trial.suggest_categorical('p', [1, 2]),  # Minkowski distance parameter
        'weights': trial.suggest_categorical('weights', ['uniform', 'distance'])
    }

    model = KNeighborsClassifier(**param)
    score = cross_val_score(model, X_train_prep, y_train, cv=3, scoring='roc_auc').mean()

    return score

knn_study = optuna.create_study(direction='maximize')
knn_study.optimize(knn_objective, n_trials=200, timeout=1800)
print('Best parameters for KNN:', knn_study.best_params)
print('Best score for KNN:', knn_study.best_value)

[I 2024-10-23 22:09:55,889] A new study created in memory with name: no-name-89a43184-2ef2-4118-9f01-106a1aaf7c90
[I 2024-10-23 22:11:33,944] Trial 0 finished with value: 0.8857773995113046 and parameters: {'n_neighbors': 7, 'leaf_size': 35, 'p': 1, 'weights': 'uniform'}. Best is trial 0 with value: 0.8857773995113046.
[I 2024-10-23 22:13:12,487] Trial 1 finished with value: 0.8995727649892603 and parameters: {'n_neighbors': 13, 'leaf_size': 32, 'p': 1, 'weights': 'distance'}. Best is trial 1 with value: 0.8995727649892603.
[I 2024-10-23 22:13:30,490] Trial 2 finished with value: 0.8940765852991449 and parameters: {'n_neighbors': 13, 'leaf_size': 28, 'p': 2, 'weights': 'distance'}. Best is trial 1 with value: 0.8995727649892603.
[I 2024-10-23 22:15:08,183] Trial 3 finished with value: 0.8967820242079036 and parameters: {'n_neighbors': 12, 'leaf_size': 48, 'p': 1, 'weights': 'uniform'}. Best is trial 1 with value: 0.8995727649892603.
[I 2024-10-23 22:15:26,072] Trial 4 finished with val

Best parameters for KNN: {'n_neighbors': 15, 'leaf_size': 24, 'p': 1, 'weights': 'uniform'}
Best score for KNN: 0.8999919341832944


In [15]:
knn_best_params = knn_study.best_trial.params
knn_best_score = knn_study.best_trial.value
knn_best_score

0.8999919341832944

# Stacking

In [16]:
from sklearn.ensemble import StackingClassifier

# Init base models

xgb_model = xgb.XGBClassifier(**xgb_best_params)
try:
    cat_model = CatBoostClassifier(**cat_best_params)
except Exception as e:
    print(e)
    
lgb_model = lgb.LGBMClassifier(**lgb_best_params)
extratrees_model = ExtraTreesClassifier(**extratrees_best_params)
# logreg_model = LogisticRegression(**logreg_best_params)
histgb_model = HistGradientBoostingClassifier(**histgb_best_params)
knn_model = KNeighborsClassifier(**knn_best_params)

# Base and meta models
try:
    base_estimators = [
    	('xgb', xgb_model),
    	('cat', cat_model),
    	('lgb', lgb_model),
    	('extratrees', extratrees_model),
    	('histgb', histgb_model),
    	('knn', knn_model)
    ]
except:
    base_estimators = [
    	('xgb', xgb_model),
    	# ('cat', cat_model),
    	('lgb', lgb_model),
    	('extratrees', extratrees_model),
    	('histgb', histgb_model),
    	('knn', knn_model)
    ]
    
meta_model = lgb.LGBMClassifier()

# Stack

stack_model = StackingClassifier(estimators=base_estimators, final_estimator=meta_model, cv=3, n_jobs=-1)

stack_model.fit(X_train_prep, y_train)

name 'cat_best_params' is not defined
[LightGBM] [Warning] min_gain_to_split is set=0.0038687550899640334, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.0038687550899640334
[LightGBM] [Warning] min_gain_to_split is set=0.0038687550899640334, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.0038687550899640334
[LightGBM] [Info] Number of positive: 11630, number of negative: 58086
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.022620 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 957
[LightGBM] [Info] Number of data points in the train set: 69716, number of used features: 20
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.166820 -> initscore=-1.608337
[LightGBM] [Info] Start training from score -1.608337
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf

StackingClassifier(cv=3,
                   estimators=[('xgb',
                                XGBClassifier(alpha=1.1931032382768336,
                                              base_score=None, booster=None,
                                              callbacks=None,
                                              colsample_bylevel=None,
                                              colsample_bynode=None,
                                              colsample_bytree=0.6824653208322442,
                                              device=None,
                                              early_stopping_rounds=None,
                                              enable_categorical=False,
                                              eval_metric=None,
                                              feature_types=None,
                                              gamma=0.27886770251477494,
                                              grow_policy=None,...
                                                     max_features=0.8721858323954309,
                                                     min_samples_split=7,
                                                     n_estimators=170)),
                               ('histgb',
                                HistGradientBoostingClassifier(l2_regularization=0.0010994373016020706,
                                                               learning_rate=0.05241807549870634,
                                                               max_depth=12,
                                                               max_iter=320,
                                                               max_leaf_nodes=45,
                                                               min_samples_leaf=46)),
                               ('knn',
                                KNeighborsClassifier(leaf_size=24,
                                                     n_neighbors=15, p=1))],
                   final_estimator=LGBMClassifier(), n_jobs=-1)

In [17]:
print('Stacking Classifier ROC AUC:', roc_auc_score(y_test, stack_model.predict_proba(X_test_prep)[:, 1]))

[LightGBM] [Warning] min_gain_to_split is set=0.0038687550899640334, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.0038687550899640334
Stacking Classifier ROC AUC: 0.9597858047563181


# Submission

In [18]:
X_train_all = preprocessor.transform(X)

stack_model = StackingClassifier(estimators=base_estimators, final_estimator=meta_model, cv=5, n_jobs=-1)

stack_model.fit(X_train_all, y)

[LightGBM] [Warning] min_gain_to_split is set=0.0038687550899640334, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.0038687550899640334
[LightGBM] [Warning] min_gain_to_split is set=0.0038687550899640334, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.0038687550899640334
[LightGBM] [Info] Number of positive: 14538, number of negative: 72608
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.020207 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 961
[LightGBM] [Info] Number of data points in the train set: 87146, number of used features: 20
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.166823 -> initscore=-1.608309
[LightGBM] [Info] Start training from score -1.608309
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further split

StackingClassifier(cv=5,
                   estimators=[('xgb',
                                XGBClassifier(alpha=1.1931032382768336,
                                              base_score=None, booster=None,
                                              callbacks=None,
                                              colsample_bylevel=None,
                                              colsample_bynode=None,
                                              colsample_bytree=0.6824653208322442,
                                              device=None,
                                              early_stopping_rounds=None,
                                              enable_categorical=False,
                                              eval_metric=None,
                                              feature_types=None,
                                              gamma=0.27886770251477494,
                                              grow_policy=None,...
                                                     max_features=0.8721858323954309,
                                                     min_samples_split=7,
                                                     n_estimators=170)),
                               ('histgb',
                                HistGradientBoostingClassifier(l2_regularization=0.0010994373016020706,
                                                               learning_rate=0.05241807549870634,
                                                               max_depth=12,
                                                               max_iter=320,
                                                               max_leaf_nodes=45,
                                                               min_samples_leaf=46)),
                               ('knn',
                                KNeighborsClassifier(leaf_size=24,
                                                     n_neighbors=15, p=1))],
                   final_estimator=LGBMClassifier(), n_jobs=-1)

In [19]:
import joblib

try:
    joblib.dump(stack_model, '../models/stack_model_v9.pkl')
except:
    joblib.dump(stack_model, 'stack_model_v9.pkl')
    
X_to_pred = preprocessor.transform(data_to_predict)
y_pred_submit = stack_model.predict_proba(X_to_pred)[:, 1]

submission = pd.DataFrame({'id': data_to_predict['id'], 'loan_status': y_pred_submit})
try:
    submission.to_csv('../submissions/stack_model_v9.csv', index=False)
except:
    submission.to_csv('stack_model_v9.csv', index=False)

[LightGBM] [Warning] min_gain_to_split is set=0.0038687550899640334, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.0038687550899640334
